# Linear Model Regression with MC Stan

This notebook implements a mock data study, where noisy data is analyzed using different models with
increasing numebrs of parameters. The AIC information criterion is used to assess the model predictivity
and to carry out a model averaging.

# Import the necessary libraries 

In [ ]:
#Numerical Routines and arrays
import numpy as np

#Graph Plotting
import matplotlib.pyplot as plt
import matplotlib.mlab as mlab

#Statistical Analysis of MCStan output
import arviz as az
import xarray as xr
xr.set_options(display_expand_data=False, display_expand_attrs=False);

# Initiate Stan via cmdstanpy (Python interface for cmdstan)

In [ ]:
import os
from cmdstanpy import CmdStanModel, cmdstan_path

# Prepare the mock Data
In this simple example we will consider only a single predictor x which generates the observations y.

In [ ]:
xmin=0; xmax=10;

Nsamp=40;

MockX = np.sort(np.random.uniform(xmin,xmax,Nsamp));

print(MockX)

σ=1; a=1; b=3.1412; c=-0.2543

MockData=np.array([ a + b*MockX[l] + c*MockX[l]**2 for l  in range(Nsamp) ] + np.random.normal(0,σ,Nsamp)) ;

plt.plot(MockX,MockData,'o')

In [ ]:
MockDataStan={'N':Nsamp,'x':MockX,'y':MockData};

# Setting up the MC Stan Models

here we will not specify a prior on the model parameters, which means that MC Stan will use a uniform prior automatically.

In [ ]:
stanM0 = """
data
  {
    int<lower = 0> N;
    vector[N] x;
    vector[N] y;
  }
parameters
  {
    real a;
    real<lower = 0> s;
  }
model {
    y ~normal(a, s);
  }
generated quantities {
  vector[N] log_lik;
  vector[N] pst_prd;
  for (n in 1:N) {
    log_lik[n] = normal_lpdf(y[n] | a , s);
    pst_prd[n] = normal_rng(a,s);
  }
}
""";
with open("modelM0.stan", "w") as file:
    file.write(stanM0)

In [ ]:
stanM1 = """
data
  {
    int<lower = 0> N;
    vector[N] x;
    vector[N] y;
  }
parameters
  {
    real a;
    real b;
    real<lower = 0> s;
  }
model {
    y ~normal(a + b * x, s);
  }
generated quantities {
  vector[N] log_lik;
  vector[N] pst_prd;
  for (n in 1:N) {
    log_lik[n] = normal_lpdf(y[n] | a + b*x[n] , s);
    pst_prd[n] = normal_rng(a + b*x[n],s);
  }
}  
""";
with open("modelM1.stan", "w") as file:
    file.write(stanM1)

In [ ]:
stanM2 = """
data
  {
    int<lower = 0> N;
    vector[N] x;
    vector[N] y;
  }
parameters
  {
    real a;
    real b;
    real c;
    real<lower = 0> s;
  }
model {
    y ~normal(a + b*x + c*x^2, s);
  }
generated quantities {
  vector[N] log_lik;
  vector[N] pst_prd;
  for (n in 1:N) {
    log_lik[n] = normal_lpdf(y[n] | a + b*x[n] + c*x[n]^2 , s);
    pst_prd[n] = normal_rng(a + b*x[n] + c*x[n]^2,s);
  }
}    
""";
with open("modelM2.stan", "w") as file:
    file.write(stanM2)

In [ ]:
stanM3 = """
data
  {
    int<lower = 0> N;
    vector[N] x;
    vector[N] y;
  }
parameters
  {
    real a;
    real b;
    real c;
    real d;
    real<lower = 0> s;
  }
model {
    y ~normal(a + b*x + c*x^2 + d*x^3, s);
  }
generated quantities {
  vector[N] log_lik;
  vector[N] pst_prd;
  for (n in 1:N) {
    log_lik[n] = normal_lpdf(y[n] | a + b*x[n] + c*x[n]^2 + d*x[n]^3, s);
    pst_prd[n] = normal_rng( a + b*x[n] + c*x[n]^2 + d*x[n]^3,s);
  }
} 
""";
with open("modelM3.stan", "w") as file:
    file.write(stanM3)

In [ ]:
stanM4 = """
data
  {
    int<lower = 0> N;
    vector[N] x;
    vector[N] y;
  }
parameters
  {
    real a;
    real b;
    real c;
    real d;
    real e;
    real<lower = 0> s;
  }
model {
    y ~normal(a + b*x + c*x^2 + d*x^3 + e*x^4, s);
  }
generated quantities {
  vector[N] log_lik;
  vector[N] pst_prd;
  for (n in 1:N) {
    log_lik[n] = normal_lpdf(y[n] | a + b*x[n] + c*x[n]^2 + d*x[n]^3 + e*x[n]^4, s);
    pst_prd[n] = normal_rng( a + b*x[n] + c*x[n]^2 + d*x[n]^3 + e*x[n]^4,s);
  }
} 
""";
with open("modelM4.stan", "w") as file:
    file.write(stanM4)

In [ ]:
modelM0=CmdStanModel(stan_file='./modelM0.stan', cpp_options={'STAN_THREADS':'true'});
modelM1=CmdStanModel(stan_file='./modelM1.stan', cpp_options={'STAN_THREADS':'true'});
modelM2=CmdStanModel(stan_file='./modelM2.stan', cpp_options={'STAN_THREADS':'true'});
modelM3=CmdStanModel(stan_file='./modelM3.stan', cpp_options={'STAN_THREADS':'true'});
modelM4=CmdStanModel(stan_file='./modelM4.stan', cpp_options={'STAN_THREADS':'true'});

# Warmup: Maximum Liklihood estimation

first without modelling errorbars on the input data 

In [ ]:
MLEM0=modelM0.optimize(data=MockDataStan)
MLEM1=modelM1.optimize(data=MockDataStan)
MLEM2=modelM2.optimize(data=MockDataStan)
MLEM3=modelM3.optimize(data=MockDataStan)
MLEM4=modelM4.optimize(data=MockDataStan)

In [ ]:
print("Model M0")
print(MLEM0.optimized_params_pd);
print("Model M1")
print(MLEM1.optimized_params_pd);
print("Model M2")
print(MLEM2.optimized_params_pd);
print("Model M3")
print(MLEM3.optimized_params_pd);
print("Model M4")
print(MLEM4.optimized_params_pd);

In [ ]:
plt.plot(MockX,MockData,'o')
plt.plot( MockX, [ MLEM0.optimized_params_pd.a for i in range(len(MockX)) ], label='M0' )
plt.plot( MockX, [ MLEM1.optimized_params_pd.a + MLEM1.optimized_params_pd.b*MockX[i] for i in range(len(MockX)) ], label='M1' )
plt.plot( MockX, [ MLEM2.optimized_params_pd.a + MLEM2.optimized_params_pd.b*MockX[i] + MLEM2.optimized_params_pd.c*pow(MockX[i],2) for i in range(len(MockX)) ], label='M2' )
plt.plot( MockX, [ MLEM3.optimized_params_pd.a + MLEM3.optimized_params_pd.b*MockX[i] + MLEM3.optimized_params_pd.c*pow(MockX[i],2) + MLEM3.optimized_params_pd.d*pow(MockX[i],3) for i in range(len(MockX)) ], label='M3' )
plt.plot( MockX, [ MLEM4.optimized_params_pd.a + MLEM4.optimized_params_pd.b*MockX[i] + MLEM4.optimized_params_pd.c*pow(MockX[i],2) + MLEM4.optimized_params_pd.d*pow(MockX[i],3) + MLEM4.optimized_params_pd.e*pow(MockX[i],4) for i in range(len(MockX)) ], label='M4' )
plt.legend()

# Clear change from underfitting (M0,M1) to (over?)fitting (M2,M3,M4)


# As next step we will sample from the posterior

In [ ]:
StanMCM0 = modelM0.sample(data=MockDataStan, chains=4, parallel_chains=2, show_console=True, iter_warmup=1000, iter_sampling=2000)
StanMCM1 = modelM1.sample(data=MockDataStan, chains=4, parallel_chains=2, show_console=True, iter_warmup=1000, iter_sampling=2000)
StanMCM2 = modelM2.sample(data=MockDataStan, chains=4, parallel_chains=2, show_console=True, iter_warmup=1000, iter_sampling=2000)
StanMCM3 = modelM3.sample(data=MockDataStan, chains=4, parallel_chains=2, show_console=True, iter_warmup=1000, iter_sampling=2000)
StanMCM4 = modelM4.sample(data=MockDataStan, chains=4, parallel_chains=2, show_console=True, iter_warmup=1000, iter_sampling=2000)

# Make the sampled data from MC Stan accessible to Python via ArviZ

In [ ]:
cmdstanpy_dataM0 = az.from_cmdstanpy(
    posterior=StanMCM0,
    posterior_predictive="pst_prd",
    observed_data={"y": MockData},
    log_likelihood="log_lik",
    coords={"x": np.arange(Nsamp)},
    dims={
        "y" : ["x"] ,
        "log_lik" : ["x"],
        "pst_prd" : ["x"],
    },
);
cmdstanpy_dataM1 = az.from_cmdstanpy(
    posterior=StanMCM1,
    posterior_predictive="pst_prd",
    observed_data={"y": MockData},
    log_likelihood="log_lik",
    coords={"x": np.arange(Nsamp)},
    dims={
        "y" : ["x"] ,
        "log_lik" : ["x"],
        "pst_prd" : ["x"],
    },
);
cmdstanpy_dataM2 = az.from_cmdstanpy(
    posterior=StanMCM2,
    posterior_predictive=["pst_prd"],
    observed_data={"y": MockData},
    log_likelihood=["log_lik"],
    coords={"x": np.arange(Nsamp)},
    dims={
        "y" : ["x"] ,
        "log_lik" : ["x"],
        "pst_prd" : ["x"],
    },
);
cmdstanpy_dataM3 = az.from_cmdstanpy(
    posterior=StanMCM3,
    posterior_predictive="pst_prd",
    observed_data={"y": MockData},
    log_likelihood="log_lik",
    coords={"x": np.arange(Nsamp)},
    dims={
        "y" : ["x"] ,
        "log_lik" : ["x"],
        "pst_prd" : ["x"],
    },
);
cmdstanpy_dataM4 = az.from_cmdstanpy(
    posterior=StanMCM4,
    posterior_predictive="pst_prd",
    observed_data={"y": MockData},
    log_likelihood="log_lik",
    coords={"x": np.arange(Nsamp)},
    dims={
        "y" : ["x"] ,
        "log_lik" : ["x"],
        "pst_prd" : ["x"],
    },
);

# Use ArviZ to compute the information criteria for the different models

   (either WAIC or LOO see https://arxiv.org/abs/1507.04544 and https://arxiv.org/abs/1507.02646 )

In [ ]:
looM0=az.loo(cmdstanpy_dataM0)
looM1=az.loo(cmdstanpy_dataM1)
looM2=az.loo(cmdstanpy_dataM2)
looM3=az.loo(cmdstanpy_dataM3)
looM4=az.loo(cmdstanpy_dataM4)

In [ ]:
print(looM0)
print(looM1)
print(looM2)
print(looM3)
print(looM4)

# Now use information criteria to compute model weights

In [ ]:
model_data = {"M0": cmdstanpy_dataM0, "M1": cmdstanpy_dataM1, "M2": cmdstanpy_dataM2, "M3": cmdstanpy_dataM3, "M4": cmdstanpy_dataM4}
az.compare(model_data, ic="loo", method="stacking")

# Let's have a look at the posterior histograms for the individual parameters

In [ ]:
Model2_Data=az.extract(cmdstanpy_dataM2)
plt.hist(Model2_Data.a.values)
plt.hist(Model2_Data.b.values)
plt.hist(Model2_Data.c.values)


In [ ]:
az.plot_posterior(cmdstanpy_dataM2)

In [ ]:
az.plot_pair(cmdstanpy_dataM2,
            var_names=['a', 'b','c','s'],
            kind='kde',
            filter_vars="regex",
            divergences=True,
            textsize=18)

# Now model the measurment errors explicitly

In [ ]:
xmin=0; xmax=10;

Nemsemble=1000;

Nsamp=40;

MockX = np.sort(np.random.uniform(xmin,xmax,Nsamp));

print(MockX)

σ=0.5; a=1; b=3.1412; c=-0.2543

MockDataIdeal=np.array([ a + b*MockX[l] + c*MockX[l]**2 for l  in range(Nsamp) ]);
RelativeErr=np.array([ 0.5*((8.)**(1/Nsamp))**l for l  in range(Nsamp) ]);                       
    
MockDataRaw= np.array( [MockDataIdeal + RelativeErr*np.random.normal(0,σ*np.sqrt(Nemsemble),Nsamp) for k in range(Nemsemble)]) ;


MockEData=np.average(MockDataRaw,axis=0)
MockEStd=np.std(MockDataRaw,axis=0)/np.sqrt(Nemsemble)

plt.errorbar(MockX,MockEData,yerr=MockEStd,fmt='o')

In [ ]:
MockEDataStan={'N':Nsamp,'x':MockX,'yObs':MockEData, 'yStd':MockEStd};

In [ ]:
stanM2E = """
data
  {
    int<lower = 0> N;
    vector[N] x;
    vector[N] yObs;
    vector[N] yStd;
  }
parameters
  {
    real a;
    real b;
    real c;
    real<lower = 0> s;
    vector[N] yEst;
  }
model {
    yEst ~normal(a + b*x + c*x^2, s);
    yObs ~normal(yEst,yStd);
    
  }
generated quantities {
  vector[N] log_lik;
  vector[N] pst_prd;
  for (n in 1:N) {
    log_lik[n] = normal_lpdf(yEst[n] | a + b*x[n] + c*x[n]^2 , s);
    pst_prd[n] = normal_rng(a + b*x[n] + c*x[n]^2,s);
  }
}    
""";
with open("modelM2E.stan", "w") as file:
    file.write(stanM2E)

In [ ]:
modelM2E=CmdStanModel(stan_file='./modelM2E.stan', cpp_options={'STAN_THREADS':'true'});

In [ ]:
StanMCM2E = modelM2E.sample(data=MockEDataStan, chains=4, parallel_chains=2, show_console=True, iter_warmup=1000, iter_sampling=5000 )

In [ ]:
cmdstanpy_dataM2E = az.from_cmdstanpy(
    posterior=StanMCM2E,
    posterior_predictive=["pst_prd"],
    observed_data={"yObs": MockData},
    log_likelihood=["log_lik"],
    coords={"x": np.arange(Nsamp)},
    dims={
        "yEst" : ["x"] ,
        "log_lik" : ["x"],
        "pst_prd" : ["x"],
    },
);

In [ ]:
Model2E_Data=az.extract(cmdstanpy_dataM2E)
plt.hist(Model2_Data.a.values)
plt.hist(Model2_Data.b.values)
plt.hist(Model2_Data.c.values)

In [ ]:
az.plot_posterior(cmdstanpy_dataM2E)

In [ ]:
az.plot_pair(cmdstanpy_dataM2E,
            var_names=['a', 'b','c','s'],
            kind='kde',
            divergences=True,
            textsize=18)